---

# S06E00 : Concurrency - Introduction to concurrency with Python

Cyril Desjouy

--- 

## 1. Introduction


Extrait de [wikipedia](https://en.wikipedia.org/wiki/Concurrency_(computer_science)):

>*In computer science, **concurrency** is the ability of different parts or units of a program, algorithm, or problem to be executed out-of-order or in partial order, without affecting the final outcome. This allows for parallel execution of the concurrent units, which can significantly improve overall speed of the execution in multi-processor and multi-core systems.*

Dans le cadre d'opérations *synchrones*, les différentes parties d'un programme sont exécutées les unes à la suite des autres. Une tâche, lorsqu'elle a été planifiée, doit s'exécuter complétement avant de pouvoir passer à l'exécution de la tâche suivante. Les opérations sont dîtes *bloquante* et doivent donc se succéder. Dans le cadre d'opérations *asynchrones*, les différentes parties d'un programme peuvent être exécutées de manière concurrente. Les opérations sont alors *non bloquantes*. Une *tâche* peut en effet commencer son exécution alors qu'une autre n'a pas encore terminé la sienne. C'est ce principe qui est désigné par le terme *concurrence* en informatique.

En d'autres termes, la *concurrence* implique que plusieurs *tâches* progressent ensemble. Sous Python, il existe deux formes de *concurrence* illustrées à la figure 1 et précisées ci-après.

* Plusieurs *tâches* s'exécutent de manière **parallèle**, en même temps: on parle alors de **processus** (***process***) et de ***multiprocessing***.
* Plusieurs *tâches* s'exécutent de manière **alternée**, se relayant: on parle alors de **fil d'exécution** (***thread***) et de ***threading***.


```
                     ┌─────────────────────────────────────────────────────────┐
                     │        ┌──────────┐┌──────────┐┌────────┐┌─────────────┐│
       Threads:      ╞<Core 1>╡ Thread 1 ╞╡ Thread 2 ╞╡Thread 1╞╡  Thread 3   ╞╡
                     │        └──────────┘└──────────┘└────────┘└─────────────┘│
                     └─────────────────────────────────────────────────────────┘

                     ┌─────────────────────────────────────────────────────────┐
                     │        ┌─────────────┐┌─────────────┐┌────────────┐     │
                     ╞<Core 1>╡  Process 1  ╞╡  Process 3  ╞╡  Process 5 ╞══>══╡
       Processes:    │        └─────────────┘└─────────────┘└────────────┘     │
                     │        ┌───────────────┐┌─────────────────────────────--│
                     ╞<Core 2>╡   Process 2   ╞╡        Process 4              │
                     │        └───────────────┘└─────────────────────────────--│
                     └─────────────────────────────────────────────────────────┘
                                   Fig. 1: Threads vs. processes
```

## 2. `threading` et `asyncio`

### 2.1. Note sur le ***GIL***

Python supporte l'utilisation de *threads* depuis ses débuts grâce au module `threading` fourni dans la bibliothèque standard. Les *threads* permettent d'exécuter des tâches de manière concurrente, mais **pas en parallèle**. Cette limitation vient de l'implémentation même de CPython et d'un mécanisme appelé ***GIL*** (Global Interpreter Lock) qui est un verrou empêchant l'exécution simultanée de ***threads***. En d'autre termes, le ***GIL*** s'assure qu'un seul ***thread*** est actif à chaque instant. L'interpréteur Python peut cependant basculer d'un ***thread*** à l'autre pour leur permettre de s'exécuter de manière concurrente.

Pour en savoir plus sur le *pourquoi* et *comment* du ***GIL***, un article très bien écrit est disponible sur [realpython.org](https://realpython.com/python-gil/).

### 2.2. Les threads

Sous Python, la gestion des *threads* est donc founie par le module `threading`. L'avantage des *threads* est qu'ils sont relativement simples à mettre en place et qu'ils partagent le même espace mémoire. Tous les *threads* issus d'un même *processsus* peuvent donc lire et écrire efficacement les mêmes données. Sachant cela, il convient bien sûr d'être vigilent sur l'accès aux données quand on manipule plusieurs *threads*.


### 2.2. Les coroutines

Comme nous l'avons vu, il est possible d'implémenter des tâches non bloquantes à l'aide de *threads*. Une autre idée consiste à reprendre le principe des générateurs qui utilisent le mot clé `yield` pour suspendre de manière non bloquante l'exécution d'une fonction génératrice. C'est à partir de ce mécanisme que son nées les coroutines sous Python et le module `asyncio`. Le principe de base de `asyncio` est d'utiliser une boucle d'événements possédant une file d'attente depuis laquelle la boucle tire les tâches et les exécute.

C'est finalement la manière dont les *threads* (ou les tâches dans le cas de `asyncio`) se succèdent qui fait la vraie différence entre `threading` et `asyncio`. Quand on utilise `threading`, c'est le système d'exploitation qui gére la planification des *threads* et peut les interrompre à tout moment pour en lancer des différents. C'est ce qu'on appelle le *multitâche préventif*. Quand on utilise `asyncio`, les tâches doivent coopérer en annonçant quand elles sont prêtes à être remplacées. C'est ce qu'on appelle le *multitâche coopératif*.

## 3. Comment contourner le ***GIL*** ?

### 3.1. `multiprocessing`

Comme nous l'avons vu précédemment, les *threads* sous Python ne peuvent pas s'exécuter en parallèle. 
L'approche la plus directe pour faire du calcul parallèle sous Python est d'utiliser des *processus*. Un *processus* peut être vu comme un *programme indépendant* s'exécutant dans son propre interpréteur Python. Chaque processus a donc ses ressources propres (CPU, mémoire) et peut bien sûr avoir plusieurs *thread*.
Différents processus peuvent s'exécuter simultanément dans différents interpréteurs sans interférer puisqu'ils utilisent des ressources isolées. On parle alors de ***multiprocessing***. Sous Python, pour utiliser des *processus* on utilise le module éponyme `multiprocessing`. 

Il est important de préciser qu'il y a certains désavantages à utiliser des *processus*:

* Le partage de données entre les *processus* est plus lent et complexe qu'entre *threads* puisque les *processus* ne partage pas l'espace mémoire (il faut donc du temps I/O pour passer les informations entre *processus*).
* L'ouverture et la clôture de *processus* prend plus de temps que celles des *threads* puisqu'il s'agit *"relancer un interpréteur"* pour chaque *processus*.

### 3.2. Les autres possibilités

Certains langages n'ont pas cette limitation qu'impose le ***GIL*** sur l'exécution simultanée de *threads*. C'est le cas par exemple de <i>C</i>, <i>C++</i> ou *Fortran* qui peuvent facilement être interfacés avec Python (Cf. python C API, module f2py, ...). La solution la plus généralement adoptée est cependant l'utilisation du module `cython` qui fournit des outils permettant de lever localement le ***GIL*** et donc de proposer du <i><b>multi</b>-threading</i> directement sous Python (via *openMP*).

## 4. Conclusion

### 4.1. CPU bound vs. I/O bound

Tous les types de programmation concurrente proposés par Python sont utiles. Encore faut il savoir quel type utiliser pour quelle tâche. En informatique, on peut distinguer deux types de tâches:

* les **tâches liées aux I/O** comme par exemple la *communication avec un périphérique lent* (connexion réseau, périphérique de stockage, ...)<br>
    => accélération possible en superposant les temps d'attente des périphériques.

* les **tâches liées au CPU** comme par exemple des *opérations mathématiques*:<br>
    => accélération possible en multipliant les unités de calcul (les processeurs).

De ce fait, on aura tendance à utiliser des ***processus*** pour des applications liées au ***processeurs*** et des ***threads*** pour des applications liées aux ***I/O***. La règle suivante est généralement pertinente:

* tâches liée au CPU :`multiprocessing`, `cython` (et `mpi4py` pour les cluster de calcul)
* tâches liées aux I/O rapides avec peu de connections: `threading`
* tâches liées aux I/O lentes avec beaucoup de connections: `asyncio`

Quel que soit le type de *concurrence* utilisé, il est important de garder à l'esprit que la programmation concurrente entraîne une couche supplémentaire de complexité. Il est donc indispensable d'évaluer si l'accélération potentielle vaut la peine d'un effort supplémentaire. 

### 4.2. Au menu

L'objectif de cette série de notebooks n'est pas de couvrir toutes les possibilités offertes par Python en termes de programmation concurrente. De nombreux modules développés par la communauté sont en effet dédiés à la programmation concurrente comme précisé sur la page [concurrency du wiki officiel de python](https://wiki.python.org/moin/Concurrency/). L'objectif ici est davantage de fournir quelques clés concernant les modules classiquement utilisés en programmation concurrente sous Python. Les différentes notions abordées sont donc:

* Le module `multiprocessing` ou comment utiliser les *processus* ?
* Le module `threading` ou comment utiliser les *threads* ?
* Les primitives de synchronisation ou comment synchroniser les *threads* et les *processus* ?
* Le module `concurrent.futures` ou comment simplifier la gestion des *threads* et des *processus* pour des applications simples ?
* Le module `asyncio`ou comment utiliser les *coroutines* ?
* Le module `cython`ou comment optimiser des codes scientifiques et se servir de *cython* pour lever le ***GIL*** ?
* Le module `mpi4py` ou comment lancer des *processus* sur plusieurs machines ayant chacune plusieurs processeurs ?

## Bibliographie

* [Realpython.org - Concurrency](https://realpython.com/python-concurrency/)
* [Masnun - Forms of concurrency](http://masnun.rocks/2016/10/06/async-python-the-different-forms-of-concurrency/)